# Importing libraries

In [29]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import altair as alt

# Importing data

In [67]:
# Importing LightGBM results
LGBM_no_sent = pd.read_csv('../datasets/processed_data/model_predictions/LightGBM/woSentiment/ELGIEQUIP.BO.csv')
LGBM_w_sent = pd.read_csv('../datasets/processed_data/model_predictions/LightGBM/wSentiment/ELGIEQUIP.BO.csv')

In [68]:
# Importing Prophet results
Prophet = pd.read_csv('../datasets/processed_data/model_predictions/Prophet/ELGIEQUIP.BO.csv')

In [69]:
# Importing RF results
RF_no_sent = pd.read_csv('random_forest/rf_ELGIEQUIP_without_sentiment.csv')
RF_w_sent = pd.read_csv('random_forest/rf_ELGIEQUIP.csv')

In [70]:
# Importing LSTM results
LSTM = pd.read_csv('../datasets/processed_data/model_predictions/LSTM/ELGIEQUIP_LSTM_predictions.csv')

In [71]:
# Linear Regression results
LR_no_sent = pd.read_csv('linear_regression/lr_ELGIEQUIP_without_sentiment.csv')
LR_w_sent = pd.read_csv('linear_regression/lr_ELGIEQUIP.csv')

# Combining datasets

## LSTM predictions outcome

In [72]:
LSTM.shape

(740, 4)

In [73]:
LSTM.head()

date  Actual High  Predicted high LSTM (no sentiments)  \
0  2021-11-08   205.600006                           203.016385   
1  2021-11-08   205.600006                           202.586307   
2  2021-11-08   205.600006                           202.233535   
3  2021-11-08   205.600006                           207.076712   
4  2021-11-08   205.600006                           206.638033   

   Predicted high LSTM (with sentiments)  
0                             209.622623  
1                             209.880580  
2                             209.609982  
3                             213.815075  
4                             214.078191

## LGBM predictions outcome

In [105]:
LGBM_no_sent.tail(2)

date    high  Predicted high LGBM (no sentiments)
363  2022-01-04  314.95                              310.475
364  2022-01-05  319.70                              312.144

In [75]:
LGBM_no_sent.columns = ['date', 'high', 'Predicted high LGBM (no sentiments)']

In [76]:
LGBM_no_sent.shape

(365, 3)

In [77]:
LGBM_w_sent.head(2)

date   high  pred_high
0  2020-08-25  114.2    117.482
1  2020-08-26  113.9    115.996

In [78]:
LGBM_w_sent.columns = ['date', 'high', 'Predicted high LGBM (with sentiments)']

In [79]:
LGBM_w_sent.shape

(365, 3)

## Prophet predictions outcome

In [80]:
Prophet.head(2)

date        high  pred_high_lower  pred_high_upper  pred_high
0  2022-01-06  340.299988          331.815          343.356    337.519
1  2022-01-07  340.149994          333.303          345.103    339.104

In [81]:
Prophet.columns= ['date', 'high', 'pred_high_lower_Prophet', 'pred_high_upper_Prophet', 'Predicted high Prophet']

In [82]:
Prophet.shape

(375, 5)

## RF predictions outcome

In [83]:
RF_no_sent.head(2)

date      y_test      y_pred
0  2020-08-25  114.199997  118.762444
1  2020-08-26  113.900002  116.980728

In [84]:
RF_no_sent.columns = ['date', 'y_test', 'Predicted high RF (no sentiments)']

In [85]:
RF_no_sent.shape

(740, 3)

In [86]:
RF_w_sent.columns = ['date', 'y_test', 'Predicted high RF (with sentiments)']

In [87]:
RF_w_sent.head(2)

date      y_test  Predicted high RF (with sentiments)
0  2020-08-25  114.199997                           118.919441
1  2020-08-26  113.900002                           117.248047

In [88]:
RF_w_sent.shape

(740, 3)

## Linear regression predictions outcome

In [89]:
LR_no_sent.head(2)

date      y_test      y_pred
0  2020-08-25  114.199997  118.301923
1  2020-08-26  113.900002  116.425265

In [90]:
LR_no_sent.columns = ['date', 'high', 'Predicted high LR (no sentiments)']

In [91]:
LR_w_sent.head(2)

date      y_test      y_pred
0  2020-08-25  114.199997  118.476197
1  2020-08-26  113.900002  116.425709

In [92]:
LR_w_sent.columns = ['date', 'high', 'Predicted high LR (with sentiments)']

## Combining results into dataframe

In [93]:
df = pd.concat([RF_no_sent, RF_w_sent['Predicted high RF (with sentiments)'], 
                LGBM_no_sent['Predicted high LGBM (no sentiments)'], 
                LGBM_w_sent['Predicted high LGBM (with sentiments)'],
                LR_no_sent['Predicted high LR (no sentiments)'],
                LR_w_sent['Predicted high LR (with sentiments)']], axis=1)

In [94]:
df.head()

date      y_test  Predicted high RF (no sentiments)  \
0  2020-08-25  114.199997                         118.762444   
1  2020-08-26  113.900002                         116.980728   
2  2020-08-27  115.000000                         118.071787   
3  2020-08-28  115.675003                         118.880653   
4  2020-08-31  115.000000                         118.783576   

   Predicted high RF (with sentiments)  Predicted high LGBM (no sentiments)  \
0                           118.919441                              117.619   
1                           117.248047                              114.501   
2                           117.983763                              115.983   
3                           118.639444                              116.690   
4                           118.680642                              117.668   

   Predicted high LGBM (with sentiments)  Predicted high LR (no sentiments)  \
0                                117.482                         118.301923   
1                                115.996                         116.425265   
2                                117.057                         117.306102   
3                                117.680                         117.465682   
4                                117.494                         116.466288   

   Predicted high LR (with sentiments)  
0                           118.476197  
1                           116.425709  
2                           117.288799  
3                           117.563348  
4                           116.637782

In [95]:
# Merging results with the LSTM results
result = pd.merge(df, LSTM, how="left", on=["date", "date"])

In [96]:
result = result.drop('y_test', axis=1)

In [97]:
result.head()

date  Predicted high RF (no sentiments)  \
0  2020-08-25                         118.762444   
1  2020-08-26                         116.980728   
2  2020-08-27                         118.071787   
3  2020-08-28                         118.880653   
4  2020-08-31                         118.783576   

   Predicted high RF (with sentiments)  Predicted high LGBM (no sentiments)  \
0                           118.919441                              117.619   
1                           117.248047                              114.501   
2                           117.983763                              115.983   
3                           118.639444                              116.690   
4                           118.680642                              117.668   

   Predicted high LGBM (with sentiments)  Predicted high LR (no sentiments)  \
0                                117.482                         118.301923   
1                                115.996                         116.425265   
2                                117.057                         117.306102   
3                                117.680                         117.465682   
4                                117.494                         116.466288   

   Predicted high LR (with sentiments)  Actual High  \
0                           118.476197          NaN   
1                           116.425709          NaN   
2                           117.288799          NaN   
3                           117.563348          NaN   
4                           116.637782          NaN   

   Predicted high LSTM (no sentiments)  Predicted high LSTM (with sentiments)  
0                                  NaN                                    NaN  
1                                  NaN                                    NaN  
2                                  NaN                                    NaN  
3                                  NaN                                    NaN  
4                                  NaN                                    NaN

In [98]:
result.columns

Index(['date', 'Predicted high RF (no sentiments)',
       'Predicted high RF (with sentiments)',
       'Predicted high LGBM (no sentiments)',
       'Predicted high LGBM (with sentiments)',
       'Predicted high LR (no sentiments)',
       'Predicted high LR (with sentiments)', 'Actual High',
       'Predicted high LSTM (no sentiments)',
       'Predicted high LSTM (with sentiments)'],
      dtype='object')

In [99]:
melted_df = pd.melt(result, id_vars =['date'],
                     value_vars =['Actual High','Predicted high LSTM (no sentiments)',
                                  'Predicted high LSTM (with sentiments)',
                                 'Predicted high RF (no sentiments)', 
                                  'Predicted high RF (with sentiments)', 
                                  'Predicted high LGBM (no sentiments)', 
                                  'Predicted high LGBM (with sentiments)',
                                 'Predicted high LR (no sentiments)',
                                 'Predicted high LR (with sentiments)'],
                    var_name ='Method', value_name ='High price')

In [100]:
melted_df.head(5)

date       Method  High price
0  2020-08-25  Actual High         NaN
1  2020-08-26  Actual High         NaN
2  2020-08-27  Actual High         NaN
3  2020-08-28  Actual High         NaN
4  2020-08-31  Actual High         NaN

In [101]:
melted_df.Method.unique()

array(['Actual High', 'Predicted high LSTM (no sentiments)',
       'Predicted high LSTM (with sentiments)',
       'Predicted high RF (no sentiments)',
       'Predicted high RF (with sentiments)',
       'Predicted high LGBM (no sentiments)',
       'Predicted high LGBM (with sentiments)',
       'Predicted high LR (no sentiments)',
       'Predicted high LR (with sentiments)'], dtype=object)

In [102]:
# use the 538 theme
alt.themes.enable('fivethirtyeight')
alt.data_transformers.enable('default', max_rows=None)

DataTransformerRegistry.enable('default')

In [103]:
zoom = alt.selection_interval(encodings=["x", "y"])

palette = alt.Scale(domain=['Actual High', 'Predicted high LSTM (no sentiments)',
       'Predicted high LSTM (with sentiments)',
       'Predicted high RF (no sentiments)',
       'Predicted high RF (with sentiments)',
       'Predicted high LGBM (no sentiments)',
       'Predicted high LGBM (with sentiments)',
                           'Predicted high LR (no sentiments)','Predicted high LR (with sentiments)'],
                  range=['#330000', '#FF0000', '#0000FF', '#00FF00', '#FF8000','#663300','#808080', '#00FFFF', '#FF00FF'])

nearest = alt.selection_point(nearest=True, on='mouseover', clear='mouseout',
                        fields=['date'], empty=False)


minimap = (
    alt.Chart(melted_df)
    .mark_line()
    .add_params(zoom)
    .encode(
        x="date:T",
        y="High price:Q",
        color=alt.condition(zoom, "Method", alt.value("darkgrey")),
    )
    .properties(
        width=200,
        height=200,
        title="ELGIEQUIP 'high'price"))

# Transparent selectors across the chart. This is what tells us
# the x-value of the cursor
selectors = alt.Chart(melted_df).mark_point().encode(
    x='date:T',
    opacity=alt.value(0),
).add_params(
    nearest
)

columns = sorted(melted_df.Method.unique())
selection = alt.selection_single(
    fields=['date'], nearest=True, on='mouseover', empty='none', clear='mouseout'
)

detail = (
    alt.Chart(melted_df)
    .mark_line()
    .encode(
        alt.X("date:T").scale(domain={"param": zoom.name, "encoding": "x"}),
        alt.Y("High price:Q").scale(domain={"param": zoom.name, "encoding": "y"}),
        color = alt.Color('Method:N',scale=palette, legend=alt.Legend(labelLimit = 400)),
    )
    .properties(width=600, height=400, title="ELGIEQUIP 'high' stock price prediction results -- detail view")
)

points = detail.mark_point().transform_filter(selection)

rule = detail.transform_pivot(
    'Method', value='High price', groupby=['date']
).mark_rule().encode(
    opacity=alt.condition(selection, alt.value(0.3), alt.value(0)),
    tooltip=[alt.Tooltip(c, type='quantitative') for c in columns]
).add_selection(selection)

(detail | minimap).configure_legend(
    orient='none',direction = 'vertical',legendX = 650,  legendY = 250, offset=-200,
    symbolDirection='vertical',
        titleFontSize=16,
        labelFontSize=14
    ).configure_title(fontSize=18)



/Users/shamil/opt/anaconda3/lib/python3.9/site-packages/altair/utils/deprecation.py:65: AltairDeprecationWarning: 'selection_single' is deprecated.  Use 'selection_point'
  warnings.warn(message, AltairDeprecationWarning, stacklevel=1)
/Users/shamil/opt/anaconda3/lib/python3.9/site-packages/altair/vegalite/v5/api.py:362: AltairDeprecationWarning: The value of 'empty' should be True or False.
  warnings.warn(
/Users/shamil/opt/anaconda3/lib/python3.9/site-packages/altair/utils/deprecation.py:65: AltairDeprecationWarning: 'add_selection' is deprecated. Use 'add_params' instead.
  warnings.warn(message, AltairDeprecationWarning, stacklevel=1)


alt.HConcatChart(...)

In [104]:
source = melted_df
zoom = alt.selection_interval(encodings=["x", "y"])

minimap = (
    alt.Chart(melted_df)
    .mark_line()
    .add_params(zoom)
    .encode(
        x="date:T",
        y="High price:Q",
        color=alt.condition(zoom, "Method", alt.value("darkgrey")),
    )
    .properties(
        width=200,
        height=200,
        ))

selectors = alt.Chart(melted_df).mark_point().encode(
    x='date:T',
    opacity=alt.value(0),
).add_params(
    nearest
)

base = alt.Chart(source).encode(x='date:T')
columns = sorted(source.Method.unique())
selection = alt.selection_single(
    fields=['date'], nearest=True, on='mouseover', empty='none', clear='mouseout'
)

lines = base.mark_line().encode(
        alt.X("date:T").scale(domain={"param": zoom.name, "encoding": "x"}),
        alt.Y("High price:Q").scale(domain={"param": zoom.name, "encoding": "y"}),
        color = alt.Color('Method:N',scale=palette, legend=alt.Legend(labelLimit = 400))
).properties(width=600, height=400, title="ELGIEQUIP 'high' stock price prediction results -- detail view")

points = lines.mark_point().transform_filter(selection)

rule = base.transform_pivot(
    'Method', value='High price', groupby=['date']
).mark_rule().encode(
    opacity=alt.condition(selection, alt.value(0.3), alt.value(0)),
    tooltip=[alt.Tooltip(c, type='quantitative') for c in columns]
).add_selection(selection)

(lines + points + rule | minimap).configure_legend(
    orient='none',direction = 'vertical',legendX = 650,  legendY = 250, offset=-200,
    symbolDirection='vertical',
        titleFontSize=16,
        labelFontSize=14
    ).configure_title(fontSize=18)

alt.HConcatChart(...)